# **TENTS FINAL**

### **Rules**

##### Original Rules

- There are exactly as many tents as trees.

- The tents and trees can be matched up in such a way that each tent is directly adjacent (horizontally or vertically, but not diagonally) to its own tree. However, a tent may be adjacent to other trees as well as its own.

- No two tents are adjacent horizontally, vertically or diagonally.

- The number of tents in each row, and in each column, matches the numbers given round the sides of the grid.

##### Additional Rules

- For tents, they have to have a space a land next to them and a tree.

- However for the tree, they have to have a water by them, for them to grow. A tent cannot be surrounded by water because they need to step out of it.

- Water must be all connected and orthogonally.

- Since there is water, there will also be water hints, BUT to keep the challenge there will only be the hints for the rows, meaning that there will be hints only in each side of the row. The hints on the left will be for water and the hints on the right will be for tents.


### **What it would look like**

This is a solved puzzle, with a minor adjustment with how this puzzle was generated.

Below I have also coded the puzzle, T is a tent, R are trees, and W is water.


<img src="unsolved_trees.png" alt="Alt Text" width="300">
<img src="solved_trees.png" alt="Alt Text" width="300">
<img src="solved_trees_with_water.png" alt="Alt Text" width="300">


In [ ]:
from itertools import permutations
from collections import deque
import random

In [154]:
blank = [['0' for i in range(8)] for i in range(8)]
blank

[['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0'],
 ['0', '0', '0', '0', '0', '0', '0', '0']]

In [155]:
blank[0][6] = 'R'
blank[1][1] = 'R'
blank[2][0] = 'R'
blank[2][5] = 'R'
blank[4][0] = 'R'
blank[4][7] = 'R'
blank[5][4] = 'R'
blank[5][7] = 'R'
blank[7][0] = 'R'
blank[7][2] = 'R'
blank[7][6] = 'R'

In [156]:
blank[0][1] = 'W'
blank[0][2] = 'W'
blank[0][3] = 'W'
blank[0][4] = 'W'
blank[0][5] = 'W'
blank[1][4] = 'W'
blank[2][4] = 'W'
blank[3][4] = 'W'
blank[3][0] = 'W'
blank[3][1] = 'W'
blank[3][2] = 'W'
blank[3][3] = 'W'
blank[3][5] = 'W'
blank[3][6] = 'W'
blank[4][3] = 'W'
blank[4][6] = 'W'
blank[5][3] = 'W'
blank[6][1] = 'W'
blank[6][2] = 'W'
blank[6][3] = 'W'
blank[6][4] = 'W'
blank[6][5] = 'W'
blank[6][6] = 'W'
blank[6][7] = 'W'
blank[7][1] = 'W'

In [157]:
blank[0][7] = 'T'
blank[1][0] = 'T'
blank[1][2] = 'T'
blank[1][5] = 'T'
blank[3][7] = 'T'
blank[4][1] = 'T'
blank[4][4] = 'T'
blank[5][6] = 'T'
blank[6][0] = 'T'
blank[7][3] = 'T'
blank[7][5] = 'T'

In [158]:
blank

[['0', 'W', 'W', 'W', 'W', 'W', 'R', 'T'],
 ['T', 'R', 'T', '0', 'W', 'T', '0', '0'],
 ['R', '0', '0', '0', 'W', 'R', '0', '0'],
 ['W', 'W', 'W', 'W', 'W', 'W', 'W', 'T'],
 ['R', 'T', '0', 'W', 'T', '0', 'W', 'R'],
 ['0', '0', '0', 'W', 'R', '0', 'T', 'R'],
 ['T', 'W', 'W', 'W', 'W', 'W', 'W', 'W'],
 ['R', 'W', 'R', 'T', '0', 'T', 'R', '0']]

In [159]:
def get_position(board):
  positions = {}
  for i, row in enumerate(board):
    for j, item in enumerate(row):
      if item in positions.keys():
        positions[item].append((i,j))
      else:
        positions[item] = [(i,j)]
  return positions

def connecting_positions(pos, diagonal=False):
  x, y = pos[0], pos[1]
  possible_positions = [(x+1,y), (x,y+1), (x-1, y), (x, y-1)]
  if diagonal:
    possible_positions.extend([(x-1, y+1), (x-1, y-1), (x+1, y+1), (x+1, y-1)])
  return possible_positions

def dfs(node, connections, visited):
  visited.add(node)
  for position in connections.get(node, []):
    if position not in visited:
      dfs(position, connections, visited)

def is_connected(connections):
  visit = set()

  dfs(next(iter(connections)), connections, visit)

  return len(visit) == len(connections)

def tree_and_tent(connections):
  visit = set()

  count = 0
  while len(visit) != len(connections):
    for connection in connections.values():
      if len(connection) == 1:
        visit.add(connection[0])
      else:
        for pos in connection:
          if pos in visit:
            connection.remove(pos)
        if len(connection) == 1:
          visit.add(connection[0])
      count += 1
      if count > 300:
        return False
  return True

def get_view(board, row=0, column=0):
  if row:
    return board[row-1]
  elif column:
    column_view = []
    for row in board:
      column_view.append(row[column-1])
    return column_view
  
def get_hints(board):
  hints = {}
  hints['row'] = {}
  hints['column'] = {}
  hints['row']['trees'] = []
  hints['column']['trees'] = []
  hints['row']['water'] = []
  hints['column']['water'] = []
  y = len(board)
  x = len(board[0])
  for i in range(1, x+1):
    view = get_view(board, row=i)
    tree_count = 0
    water_count = 0
    for item in view:
      if item == 'T':
        tree_count += 1
      if item == 'W':
        water_count += 1
    hints['row']['trees'].append(tree_count)
    hints['row']['water'].append(water_count)
  for i in range(1, y):
    view = get_view(board, column=i)
    tree_count = 0
    water_count = 0    
    for item in view:
      if item == 'T':
        tree_count += 1
      if item == 'W':
        water_count += 1
    hints['column']['trees'].append(tree_count)
    hints['column']['water'].append(water_count)
  
  return hints


def check_valid_solution(board, hints):
  positions = get_position(board)
  valid = len(positions['R']) == len(positions['T'])
  if valid:
    pass
  else:
    print("There are not an equal amount of trees and tents")
    return False


  # Check for all trees have a water source
  for tree in positions['R']:
    for orth_tree in connecting_positions(tree):
      if orth_tree in positions['W']:
        valid = True
        break
      else:
        valid = False
    if valid == False:
      print("False at tree position", tree)
      return False
  
  # Check for all tents having open land
  for tent in positions['T']:
    for orth_tent in connecting_positions(tent):
      if orth_tent in positions['0']:
        valid = True
        break
      else:
        valid = False
    if valid == False:
      print("False at tent position", tent)
      return False
  
  # check for all tents not being next to each other
  for tent in positions['T']:
    for pos_tent in connecting_positions(tent, True):
      if pos_tent in positions['T']:
        valid = False
        print(f"Found two tents next to each other at positions {tent} and {pos_tent}")
        return False
      else:
        valid = True

  # Check if water is orthogonally connected
  water_connections = {}
  water_positions = positions['W'].copy()
  for water in positions['W']:
    temp_connections = []
    for orth_water in connecting_positions(water):
      if orth_water in water_positions:
        temp_connections.append(orth_water)
    water_connections[water] = temp_connections
  valid = is_connected(water_connections)
  if not valid:
    print("water in not connected")
    return valid

  # Check if each tent has a unique tree
  tree_tent_connections = {}
  for tent in positions['T']:
    tree_tent_connections[tent] = []
    for orth_tree in connecting_positions(tent):
      if orth_tree in positions['R']:
        tree_tent_connections[tent].append(orth_tree)
  valid = tree_and_tent(tree_tent_connections)
  if not valid:
    print("Tree and tent does not have a unique pair")
    return valid

  # Check if hints match up with puzzle
  board_hints = get_hints(board)
  valid = board_hints == hints

  return valid

In [160]:
connecting_positions((2,2))

[(3, 2), (2, 3), (1, 2), (2, 1)]

In [161]:
def change_board_to_str(board):
  str_board = ""
  for row in board:
    for item in row:
      str_board += item
  return str_board

In [ ]:

def are_w_connected(grid):
    # Find all 'W' positions
    rows, cols = len(grid), len(grid[0])
    w_positions = [(r, c) for r in range(rows) for c in range(cols) if grid[r][c] == 'W']
    if not w_positions:
        return True  # No 'W's, so they are trivially connected.

    # Directions for orthogonal movement (up, down, left, right)
    directions = [(-1, 0), (1, 0), (0, -1), (0, 1)]

    # Start BFS from the first 'W' found
    visited = set()
    queue = deque([w_positions[0]])
    visited.add(w_positions[0])

    while queue:
        r, c = queue.popleft()
        for dr, dc in directions:
            nr, nc = r + dr, c + dc
            if 0 <= nr < rows and 0 <= nc < cols and (nr, nc) not in visited:
                if grid[nr][nc] == 'W' or grid[nr][nc] == '0':  # '0' can be used as connectors
                    queue.append((nr, nc))
                    visited.add((nr, nc))

    # Check if all 'W's were visited
    return all(pos in visited for pos in w_positions)

# Example grid
grid = [
    ['W', 'W', 'W', '0', 'T', 'W', 'R', 'W'],
    ['0', 'R', '0', '0', '0', '0', '0', '0'],
    ['R', '0', '0', '0', '0', 'R', '0', '0'],
    ['0', '0', '0', '0', '0', '0', '0', '0'],
    ['R', '0', '0', '0', '0', '0', '0', 'R'],
    ['0', '0', '0', '0', 'R', '0', '0', 'R'],
    ['0', '0', '0', '0', '0', '0', '0', '0'],
    ['R', '0', 'R', '0', '0', '0', 'R', '0'],
]

grid2 = [
    ('0', 'T', 'W', 'W', 'W', 'W', 'R', 'W'),
    ['0', 'R', '0', '0', '0', '0', '0', '0'],
    ['R', '0', '0', '0', '0', 'R', '0', '0'],
    ['0', '0', '0', '0', '0', '0', '0', '0'],
    ['R', '0', '0', '0', '0', '0', '0', 'R'],
    ['0', '0', '0', '0', 'R', '0', '0', 'R'],
    ['0', '0', '0', '0', '0', '0', '0', '0'],
    ['R', '0', 'R', '0', '0', '0', 'R', '0']]

# print(are_w_connected(grid))  # Output: True or False

print(are_w_connected(grid2))
positions = get_position(grid2)

def are_w_connected_v2(grid, positions):
    # Find all 'W' positions
    rows, cols = len(grid), len(grid[0])
    w_positions = positions['W']
    if not w_positions:
        return True  # No 'W's, so they are trivially connected.

    # Start BFS from the first 'W' found
    visited = set()
    queue = deque([w_positions[0]])

    visited.add(w_positions[0])


    while queue:
        position = queue.popleft()
        for orth_water in connecting_positions(position):
            if orth_water not in visited:
                if orth_water in positions['0'] or orth_water in positions['W']:  # '0' can be used as connectors
                    queue.append(orth_water)
                    visited.add(orth_water)

    # Check if all 'W's were visited
    return all(pos in visited for pos in w_positions)

print(are_w_connected_v2(grid2, positions))

8 8
w_positions [(0, 2), (0, 3), (0, 4), (0, 5), (0, 7)]
Queue deque([(0, 2)])
visited {(0, 2)}
Popped queue 0 2
Directions -1 0
nr, nc -1 2
Directions 1 0
nr, nc 1 2
Directions 0 -1
nr, nc 0 1
Directions 0 1
nr, nc 0 3
QUEUE deque([(1, 2), (0, 3)])
Popped queue 1 2
Directions -1 0
nr, nc 0 2
Directions 1 0
nr, nc 2 2
Directions 0 -1
nr, nc 1 1
Directions 0 1
nr, nc 1 3
QUEUE deque([(0, 3), (2, 2), (1, 3)])
Popped queue 0 3
Directions -1 0
nr, nc -1 3
Directions 1 0
nr, nc 1 3
Directions 0 -1
nr, nc 0 2
Directions 0 1
nr, nc 0 4
QUEUE deque([(2, 2), (1, 3), (0, 4)])
Popped queue 2 2
Directions -1 0
nr, nc 1 2
Directions 1 0
nr, nc 3 2
Directions 0 -1
nr, nc 2 1
Directions 0 1
nr, nc 2 3
QUEUE deque([(1, 3), (0, 4), (3, 2), (2, 1), (2, 3)])
Popped queue 1 3
Directions -1 0
nr, nc 0 3
Directions 1 0
nr, nc 2 3
Directions 0 -1
nr, nc 1 2
Directions 0 1
nr, nc 1 4
QUEUE deque([(0, 4), (3, 2), (2, 1), (2, 3), (1, 4)])
Popped queue 0 4
Directions -1 0
nr, nc -1 4
Directions 1 0
nr, nc 1 4
Di

In [194]:
def check_tents(positions, tree_tent_connections):

  for tent in positions['T']:
    # Check for all tents not being next to each other
    for pos_tent in connecting_positions(tent, True):
      if pos_tent in positions['T']:
        valid = False
        print(f"Found two tents next to each other at positions {tent} and {pos_tent}")
        return False
      else:
        valid = True

    tree_tent_connections[tent] = []
    valid = False
    for orth_tent in connecting_positions(tent):
      # Check for all tents having open land
      if orth_tent in positions['0']:
        valid = True
      else:
        if valid == True:
          pass
        else:
          valid = False
      # Check if each tent has a unique tree
      if orth_tent in positions['R']:
        tree_tent_connections[tent].append(orth_tent)
    if valid == False:
      print("False at tent position", tent)
      return False

  valid = tree_and_tent(tree_tent_connections)
  if not valid:
    print("Tree and tent does not have a unique pair")
    return valid

  return valid
  
def check_trees(positions, with_zeros=False):
  # Check for all trees have a water source
  for tree in positions['R']:
    for orth_tree in connecting_positions(tree):
      if orth_tree in positions['W']:
        valid = True
        break
      if with_zeros:
        if orth_tree in positions['0']:
          valid = True
          break
      else:
        valid = False
    if valid == False:
      print("False at tree position", tree)
      return False
  return valid
    
def check_water(positions, with_zeros=False, board=None):
  # Check if water is orthogonally connected
  if with_zeros:
    return are_w_connected_v2(board, positions)
  water_connections = {}
  zero_positions = []
  for water in positions['W']:
    temp_connections = []
    for orth_water in connecting_positions(water):
      if orth_water in positions['W']:
        temp_connections.append(orth_water)
      if with_zeros:
        zero_positions.append(orth_water)
        temp_connections.append(orth_water)
    water_connections[water] = temp_connections

  valid = is_connected(water_connections)
  if not valid:
    print("water in not connected")
    return valid
  return valid

# TODO: Check positions with zero 

def check_valid_solution_v2(board, hints, check_hints=False, partial_solution=False):
  positions = get_position(board)
  if not partial_solution:
    valid = len(positions['R']) == len(positions['T'])
    if valid:
      pass
    else:
      print("There are not an equal amount of trees and tents")
      return False

  # Check for all trees have a water source
  valid = check_trees(positions, partial_solution)
  if not valid:
    return valid
  print("Trees passed")
  # Check for all tents having open land
  # Check for all tents not being next to each other
  # Check if each tent has a unique tree
  tree_tent_connections = {}
  valid = check_tents(positions, tree_tent_connections)
  if not valid:
    return valid
  print("Tents passed")
  
  # Check if water is orthogonally connected
  valid = check_water(positions, partial_solution, board=board)
  if not valid:
    return valid
  print("Water passed")
  # Check if hints match up with puzzle
  if check_hints:
    board_hints = get_hints(board)
    valid = board_hints == hints
  
  return valid

In [195]:
def get_puzzle_from_board(completed_board):
  board = [['0' for i in range(len(completed_board[0]))] for j in range(len(completed_board))]
  tree_pos = {}
  for i, row in enumerate(completed_board):
    tree_pos[i] = []
    for j, item in enumerate(row):
      if item == "R":
        board[i][j] = 'R'
        tree_pos[i].append(j)
        
  return tree_pos, board

In [196]:
hints = get_hints(blank)
hints

{'row': {'trees': [1, 3, 0, 1, 2, 1, 1, 2], 'water': [5, 1, 1, 7, 2, 1, 7, 1]},
 'column': {'trees': [2, 1, 1, 1, 1, 2, 1], 'water': [1, 4, 3, 5, 5, 3, 3]}}

In [197]:
tree_pos, board = get_puzzle_from_board(blank)
tree_pos, puzzle_board = get_puzzle_from_board(blank)
row_clues = {}
column_clues = {}
for i, row in enumerate(board):
  
  row_clue = ""
  row_clue += 'T' * hints['row']['trees'][i]
  row_clue += "W" * hints['row']['water'][i]
  for item in row:
    if item == 'R':
      row_clue += "R"
  row_zeroes = 8 - len(row_clue)
  row_clue += "0" * row_zeroes
  row_clues[i] = row_clue

  # column_clue = ""
  # column_clue += 'T' * hints['row']['trees'][i]
  # column_clue += "W" * hints['row']['water'][i]
  # column_zeroes = 8 - len(column_clue)
  # column_clue += "0" * column_zeroes  
  # column_clues[i] = column_clue

In [198]:
row_perms = {}
for key, item in row_clues.items():
  row_perm = permutations(item, 8)
  row_perms[key] = set()
  for p in row_perm:
    in_position = True
    for pos in tree_pos[key]:
      if p[pos] != 'R':
        in_position = False
    if in_position == True:
      row_perms[key].add(p)

# column_perms = {}
# for key, item in column_clues.items():
#   column_perm = permutations(item, 8)
#   column_perms[key] = set()
#   for p in column_perm:
#     column_perms[key].add(p)
def print_board(board):
  for row in board:
    print(row)

In [199]:
# def check_partial_solution(board):
#   positions = get_position(board)

#   for tent in positions['T']:
#     for orth_tent in connecting_positions(tent):
#       if orth_tent in positions['0']:
#         valid = True
#         break
#       else:
#         valid = False
#     if valid == False:
#       print("False at tent position", tent)
#       return False

#   # check for all tents not being next to each other
#     for pos_tent in connecting_positions(tent, True):
#       if pos_tent in positions['T']:
#         valid = False
#         print(f"Found two tents next to each other at positions {tent} and {pos_tent}")
#         return False
#       else:
#         valid = True
#   return valid

In [200]:
def backtrack(clues, depth, possible_board, puzzle_board, skip_solution=[]):
  
  keys = list(clues.keys())
  if depth == len(clues):
    if possible_board in skip_solution:
      print("board is same in skip")
      return None 
    print("GOT HERE")
    hints = get_hints(possible_board)
    if check_valid_solution_v2(possible_board, hints, check_hints=True):
      return possible_board
    else:
      possible_board[depth-1] = puzzle_board[depth-1]
      return None
  
  for item in clues[keys[depth]]:
    possible_board[depth] = item
    print("depth", depth, "board")
    print_board(board)
    if check_valid_solution_v2(board, hints=None, partial_solution=True):
      result = backtrack(clues, depth+1, possible_board, puzzle_board, skip_solution)
      if result:
        return result
    else:
      possible_board[depth] = puzzle_board[depth]
  possible_board[depth] = puzzle_board[depth]
  return None

In [201]:
valid_partial =   [('0', 'T', 'W', 'W', 'W', 'W', 'R', 'W'),
                        ['0', 'R', '0', '0', '0', '0', '0', '0'],
                        ['R', '0', '0', '0', '0', 'R', '0', '0'],
                        ['0', '0', '0', '0', '0', '0', '0', '0'],
                        ['R', '0', '0', '0', '0', '0', '0', 'R'],
                        ['0', '0', '0', '0', 'R', '0', '0', 'R'],
                        ['0', '0', '0', '0', '0', '0', '0', '0'],
                        ['R', '0', 'R', '0', '0', '0', 'R', '0'],]

valid_partial2 = [('W', 'W', 'W', '0', 'T', 'W', 'R', 'W'),
                        ['0', 'R', '0', '0', '0', '0', '0', '0'],
                        ['R', '0', '0', '0', '0', 'R', '0', '0'],
                        ['0', '0', '0', '0', '0', '0', '0', '0'],
                        ['R', '0', '0', '0', '0', '0', '0', 'R'],
                        ['0', '0', '0', '0', 'R', '0', '0', 'R'],
                        ['0', '0', '0', '0', '0', '0', '0', '0'],
                        ['R', '0', 'R', '0', '0', '0', 'R', '0'],]

valid_partial3 = [('0', 'W', 'W', 'W', 'W', 'W', 'R', 'T'),
['0', 'R', '0', '0', '0', '0', '0', '0'],
['R', '0', '0', '0', '0', 'R', '0', '0'],
['0', '0', '0', '0', '0', '0', '0', '0'],
['R', '0', '0', '0', '0', '0', '0', 'R'],
['0', '0', '0', '0', 'R', '0', '0', 'R'],
['0', '0', '0', '0', '0', '0', '0', '0'],
['R', '0', 'R', '0', '0', '0', 'R', '0']]

In [202]:
is_vlaid = check_valid_solution_v2(valid_partial3, hints=None, partial_solution=True)
print(is_vlaid)

Trees passed
Tents passed
8 8
w_positions [(0, 1), (0, 2), (0, 3), (0, 4), (0, 5)]
Queue deque([(0, 1)])
visited {(0, 1)}
Popped queue (0, 1)
Directions (1, 1)
Directions (0, 2)
Directions (-1, 1)
Directions (0, 0)
QUEUE deque([(0, 2), (0, 0)])
Popped queue (0, 2)
Directions (1, 2)
Directions (0, 3)
Directions (-1, 2)
Directions (0, 1)
QUEUE deque([(0, 0), (1, 2), (0, 3)])
Popped queue (0, 0)
Directions (1, 0)
Directions (0, 1)
Directions (-1, 0)
Directions (0, -1)
QUEUE deque([(1, 2), (0, 3), (1, 0)])
Popped queue (1, 2)
Directions (2, 2)
Directions (1, 3)
Directions (0, 2)
Directions (1, 1)
QUEUE deque([(0, 3), (1, 0), (2, 2), (1, 3)])
Popped queue (0, 3)
Directions (1, 3)
Directions (0, 4)
Directions (-1, 3)
Directions (0, 2)
QUEUE deque([(1, 0), (2, 2), (1, 3), (0, 4)])
Popped queue (1, 0)
Directions (2, 0)
Directions (1, 1)
Directions (0, 0)
Directions (1, -1)
QUEUE deque([(2, 2), (1, 3), (0, 4)])
Popped queue (2, 2)
Directions (3, 2)
Directions (2, 3)
Directions (1, 2)
Directions

In [203]:
skip = []
skip.append([('0', 'W', 'W', 'W', 'W', 'W', 'R', 'T'),
                    ('T', 'R', 'T', '0', 'W', 'T', '0', '0'),
                    ('R', '0', '0', '0', 'W', 'R', '0', '0'),
                    ('W', 'W', 'W', 'W', 'W', 'W', 'W', 'T'),
                    ('R', 'T', 'W', '0', 'T', '0', 'W', 'R'),
                    ('0', '0', 'W', '0', 'R', '0', 'T', 'R'),
                    ('T', 'W', 'W', 'W', 'W', 'W', 'W', 'W'),
                    ('R', 'W', 'R', 'T', '0', 'T', 'R', '0')])

In [204]:
skip

[[('0', 'W', 'W', 'W', 'W', 'W', 'R', 'T'),
  ('T', 'R', 'T', '0', 'W', 'T', '0', '0'),
  ('R', '0', '0', '0', 'W', 'R', '0', '0'),
  ('W', 'W', 'W', 'W', 'W', 'W', 'W', 'T'),
  ('R', 'T', 'W', '0', 'T', '0', 'W', 'R'),
  ('0', '0', 'W', '0', 'R', '0', 'T', 'R'),
  ('T', 'W', 'W', 'W', 'W', 'W', 'W', 'W'),
  ('R', 'W', 'R', 'T', '0', 'T', 'R', '0')]]

In [205]:
backtrack(row_perms, 0, board, puzzle_board, skip)

depth 0 board
('W', 'T', 'W', 'W', '0', 'W', 'R', 'W')
['0', 'R', '0', '0', '0', '0', '0', '0']
['R', '0', '0', '0', '0', 'R', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '0']
['R', '0', '0', '0', '0', '0', '0', 'R']
['0', '0', '0', '0', 'R', '0', '0', 'R']
['0', '0', '0', '0', '0', '0', '0', '0']
['R', '0', 'R', '0', '0', '0', 'R', '0']
Trees passed
False at tent position (0, 1)
depth 0 board
('W', 'W', 'W', 'W', '0', 'T', 'R', 'W')
['0', 'R', '0', '0', '0', '0', '0', '0']
['R', '0', '0', '0', '0', 'R', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '0']
['R', '0', '0', '0', '0', '0', '0', 'R']
['0', '0', '0', '0', 'R', '0', '0', 'R']
['0', '0', '0', '0', '0', '0', '0', '0']
['R', '0', 'R', '0', '0', '0', 'R', '0']
Trees passed
Tents passed
8 8
w_positions [(0, 0), (0, 1), (0, 2), (0, 3), (0, 7)]
Queue deque([(0, 0)])
visited {(0, 0)}
Popped queue (0, 0)
Directions (1, 0)
Directions (0, 1)
Directions (-1, 0)
Directions (0, -1)
QUEUE deque([(1, 0), (0, 1)])
Popped queue (1, 0)
Directi

[('0', 'W', 'W', 'W', 'W', 'W', 'R', 'T'),
 ('T', 'R', 'T', '0', 'W', 'T', '0', '0'),
 ('R', '0', '0', '0', 'W', 'R', '0', '0'),
 ('W', 'W', 'W', 'W', 'W', 'W', 'W', 'T'),
 ('R', 'T', '0', 'W', 'T', '0', 'W', 'R'),
 ('0', '0', '0', 'W', 'R', '0', 'T', 'R'),
 ('T', 'W', 'W', 'W', 'W', 'W', 'W', 'W'),
 ('R', 'W', 'R', 'T', '0', 'T', 'R', '0')]

In [213]:
blank

[['0', 'W', 'W', 'W', 'W', 'W', 'R', 'T'],
 ['T', 'R', 'T', '0', 'W', 'T', '0', '0'],
 ['R', '0', '0', '0', 'W', 'R', '0', '0'],
 ['W', 'W', 'W', 'W', 'W', 'W', 'W', 'T'],
 ['R', 'T', '0', 'W', 'T', '0', 'W', 'R'],
 ['0', '0', '0', 'W', 'R', '0', 'T', 'R'],
 ['T', 'W', 'W', 'W', 'W', 'W', 'W', 'W'],
 ['R', 'W', 'R', 'T', '0', 'T', 'R', '0']]

In [ ]:
def place_tree_and_tent():
  pass

def generate_new_puzzle():
  trees_and_tents = 11
  x = 8
  y = 8
  blank_board=  [['0' for i in range(x)] for j in range(y)]
  pass